Note: you may need to restart the kernel to use updated packages.


In [12]:
import csv
import os
import time
import ujson
from random import randint
from typing import Dict, List, Any

import requests
from bs4 import BeautifulSoup
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.common.exceptions import NoSuchElementException
from webdriver_manager.chrome import ChromeDriverManager

In [4]:
def write_authors(list1, file_name):
    with open(file_name, 'w', encoding='utf-8') as f:
        for i in range(0, len(list1)):
            f.write(list1[i] + '\n')

In [59]:
def initCrawlerScraper(seed):
    # Initialize driver for Chrome
    webOpt = webdriver.ChromeOptions()
    webOpt.add_experimental_option('excludeSwitches', ['enable-logging'])
    webOpt.add_argument('--ignore-certificate-errors')
    webOpt.add_argument('--incognito')
    webOpt.add_argument('--headless')
#     webOpt.headless = True
    driver = webdriver.Chrome(ChromeDriverManager().install(), options=webOpt)
    driver.get(seed)  # Start with the original link

    Links = []  # Array with pureportal profiles URL
    pub_data = []  # To store publication information for each pureportal profile

    nextLink = driver.find_element(By.CSS_SELECTOR,".nextLink").is_enabled()
    print("Crawler has begun...")
    while (nextLink):
        page = driver.page_source
        # XML parser to parse each URL
        bs = BeautifulSoup(page, "lxml")

        # Extracting exact URL by spliting string into list
        for link in bs.findAll('a', class_='link person'):
            url = str(link)[str(link).find('https://pureportal.coventry.ac.uk/en/persons/'):].split('"')
            Links.append(url[0])
        # Click on Next button to visit next page
        try:
            if driver.find_element(By.CSS_SELECTOR,".nextLink"):
                element = driver.find_element(By.CSS_SELECTOR,".nextLink")
                driver.execute_script("arguments[0].click();", element)
            else:
                nextLink = False
        except NoSuchElementException:
            break
    print("Crawler has found ", len(Links), " pureportal profiles")
    write_authors(Links, 'Authors_URL.txt')
    
    
    print("Scraping publication data for ", len(Links), " pureportal profiles...")
    count = 0
    for link in Links:
        # Visit each link to get data
        time.sleep(1)
        print("link", link)
        result = driver.get(link)
        print(result)
        driver.get(link)
        try:
            if driver.find_elements(By.CSS_SELECTOR,".portal_link.btn-primary.btn-large"):
                element = driver.find_elements(By.CSS_SELECTOR,".portal_link.btn-primary.btn-large")
                for a in element:
                    if "research output".lower() in a.text.lower():
                        driver.execute_script("arguments[0].click();", a)
                        driver.get(driver.current_url)
                        # Get name of Author
                        name = driver.find_element(By.CSS_SELECTOR,"div[class='header person-details']>h1")
                        r = requests.get(driver.current_url)
                        # Parse all the data via BeautifulSoup
                        soup = BeautifulSoup(r.content, 'lxml')

                        # Extracting publication name, publication url, date and CU Authors
                        table = soup.find('ul', attrs={'class': 'list-results'})
                        if table != None:
                            for row in table.findAll('div', attrs={'class': 'result-container'}):
                                data = {}
                                data['name'] = row.h3.a.text
                                data['pub_url'] = row.h3.a['href']
                                date = row.find("span", class_="date")

                                rowitem = row.find_all(['div'])
                                span = row.find_all(['span'])
                                data['cu_author'] = name.text
                                data['date'] = date.text
                                print("Publication Name :", row.h3.a.text)
                                print("Publication URL :", row.h3.a['href'])
                                print("CU Author :", name.text)
                                print("Date :", date.text)
                                print("\n")
                                pub_data.append(data)
            else:
                # Get name of Author
                name = driver.find_element(By.CSS_SELECTOR,"div[class='header person-details']>h1")
                r = requests.get(link)
                # Parse all the data via BeautifulSoup
                soup = BeautifulSoup(r.content, 'lxml')
                # Extracting publication name, publication url, date and CU Authors
                table = soup.find('div', attrs={'class': 'relation-list relation-list-publications'})
                if table != None:
                    for row in table.findAll('div', attrs={'class': 'result-container'}):
                        data = {}
                        data["name"] = row.h3.a.text
                        data['pub_url'] = row.h3.a['href']
                        date = row.find("span", class_="date")
                        rowitem = row.find_all(['div'])
                        span = row.find_all(['span'])
                        data['cu_author'] = name.text
                        data['date'] = date.text
                        print("Publication Name :", row.h3.a.text)
                        print("Publication URL :", row.h3.a['href'])
                        print("CU Author :", name.text)
                        print("Date :", date.text)
                        print("\n")
                        pub_data.append(data)
        except Exception:
            continue

    print("Crawler has scrapped data for ", len(pub_data), " pureportal publications")
    driver.quit()
    # Writing all the scraped results in a file with JSON format
    with open('scraper_results.json', 'w') as f:
        ujson.dump(pub_data, f)

In [61]:
initCrawlerScraper('https://pureportal.coventry.ac.uk/en/organisations/coventry-university/persons/')

/var/folders/3y/yxfc9cms7ss262pddd2ymh_40000gp/T/ipykernel_1602/3448334347.py:9: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(ChromeDriverManager().install(), options=webOpt)


Crawler has begun...
Crawler has found  2325  pureportal profiles
Scraping publication data for  2325  pureportal profiles...
link https://pureportal.coventry.ac.uk/en/persons/aliano-abbasi
None
link https://pureportal.coventry.ac.uk/en/persons/sally-abbott
None
Publication Name : Emotional eating among adults with healthy weight, overweight and obesity: a systematic review and meta‐analysis
Publication URL : https://pureportal.coventry.ac.uk/en/publications/emotional-eating-among-adults-with-healthy-weight-overweight-and-
CU Author : Sally Abbott
Date : 3 Apr 2023


Publication Name : "Is it time to throw out the weighing scales?" Implicit weight bias among healthcare professionals working in bariatric surgery services and their attitude towards non-weight focused approaches
Publication URL : https://pureportal.coventry.ac.uk/en/publications/is-it-time-to-throw-out-the-weighing-scales-implicit-weight-bias-
CU Author : Sally Abbott
Date : Jan 2023


Publication Name : Variation and out

link https://pureportal.coventry.ac.uk/en/persons/mohamed-abdelshafy
None
Publication Name : Cross-Layer Multipath Multichannel MAC protocol for MANETs
Publication URL : https://pureportal.coventry.ac.uk/en/publications/cross-layer-multipath-multichannel-mac-protocol-for-manets
CU Author : Mohamed Abdelshafy
Date : Jun 2018


Publication Name : Performance evaluation of Receiver Directed Transmission protocol with a single transceiver in MANETs
Publication URL : https://pureportal.coventry.ac.uk/en/publications/performance-evaluation-of-receiver-directed-transmission-protocol
CU Author : Mohamed Abdelshafy
Date : 4 May 2017


Publication Name : Reliable Multipath Multi-channel Route Migration over Multi Link-Failure in Wireless Ad Hoc Networks
Publication URL : https://pureportal.coventry.ac.uk/en/publications/reliable-multipath-multi-channel-route-migration-over-multi-link-
CU Author : Mohamed Abdelshafy
Date : 23 Nov 2017


Publication Name : Resisting blackhole attacks on MANETs
Pub

CU Author : Rakib Abdur
Date : 28 Apr 2009


Publication Name : Verifying time, memory and communication bounds in systems of reasoning agents
Publication URL : https://pureportal.coventry.ac.uk/en/publications/verifying-time-memory-and-communication-bounds-in-systems-of-reas-3
CU Author : Rakib Abdur
Date : 28 Apr 2009


Publication Name : Verifying time and communication costs of rule-based reasoners
Publication URL : https://pureportal.coventry.ac.uk/en/publications/verifying-time-and-communication-costs-of-rule-based-reasoners
CU Author : Rakib Abdur
Date : 2009


Publication Name : Verifying resource requirements for distributed rule-based systems
Publication URL : https://pureportal.coventry.ac.uk/en/publications/verifying-resource-requirements-for-distributed-rule-based-system
CU Author : Rakib Abdur
Date : 2008


Publication Name : Verifying time, memory and communication bounds in systems of reasoning agents
Publication URL : https://pureportal.coventry.ac.uk/en/publications/v

Publication Name : Who ate all the pride?  Patriotic sentiment and English national football support.
Publication URL : https://pureportal.coventry.ac.uk/en/publications/who-ate-all-the-pride-patriotic-sentiment-and-english-national-fo
CU Author : Jackie Abell
Date : 24 Jan 2007


Publication Name : English identity and ethnic diversity in the context of UK constitutional change
Publication URL : https://pureportal.coventry.ac.uk/en/publications/english-identity-and-ethnic-diversity-in-the-context-of-uk-consti
CU Author : Jackie Abell
Date : 1 Jun 2006


Publication Name : Romantic Scotland, Tragic England, Ambiguous Britain: Constructions of 'the Empire' in post devolution national accounting
Publication URL : https://pureportal.coventry.ac.uk/en/publications/romantic-scotland-tragic-england-ambiguous-britain-constructions-
CU Author : Jackie Abell
Date : 19 Jun 2006


Publication Name : They’re not racist:  Prejudice denial, mitigation and suppression in dialogue
Publication URL : ht

...

link https://pureportal.coventry.ac.uk/en/persons/riddhi-sarkar-2
None
Publication Name : Additive manufacturing-based repair of IN718 superalloy and high-cycle fatigue assessment of the joint
Publication URL : https://pureportal.coventry.ac.uk/en/publications/additive-manufacturing-based-repair-of-in718-superalloy-and-high-
CU Author : Riddhi Sarkar
Date : Dec 2022


Publication Name : Characterization of Ductile Crack Growth Resistance Behaviour of Interstitial-Free Steel Sheet using Energy Dissipation Rate Parameter
Publication URL : https://pureportal.coventry.ac.uk/en/publications/characterization-of-ductile-crack-growth-resistance-behaviour-of-
CU Author : Riddhi Sarkar
Date : Aug 2021


Publication Name : Determination of ηp factor for clamped SENT thin sheet specimens of an Interstitial Free steel
Publication URL : https://pureportal.coventry.ac.uk/en/publications/determination-of-%CE%B7subpsub-factor-for-clamped-sent-thin-sheet-spec
CU Author : Riddhi Sarkar
Date : Feb 2021




link https://pureportal.coventry.ac.uk/en/persons/danial-sarwar
None
link https://pureportal.coventry.ac.uk/en/persons/shahzad-sarwar
None
link https://pureportal.coventry.ac.uk/en/persons/saud-sattar
None
link https://pureportal.coventry.ac.uk/en/persons/lopamudra-saxena
None
Publication Name : The Top 100 questions for the sustainable intensification of agriculture in India’s rainfed drylands
Publication URL : https://pureportal.coventry.ac.uk/en/publications/the-top-100-questions-for-the-sustainable-intensification-of-agri
CU Author : Lopamudra Saxena
Date : 2021


Publication Name : Community Self-Organisation from a Social-Ecological Perspective: ‘Burlang Yatra’ and Revival of Millets in Odisha (India)
Publication URL : https://pureportal.coventry.ac.uk/en/publications/community-self-organisation-from-a-social-ecological-perspective-
CU Author : Lopamudra Saxena
Date : 2 Mar 2020


Publication Name : Fruit & Nut Village Stirchley Project Evaluation Report
Publication URL : https:/

CU Author : Ulrich Schmutz
Date : 11 Jan 2017


Publication Name : Researching farmer perspectives on the impact of a potential increase in Nitrate Vulnerable Zones in Wales 2017
Publication URL : https://pureportal.coventry.ac.uk/en/publications/researching-farmer-perspectives-on-the-impact-of-a-potential-incr
CU Author : Ulrich Schmutz
Date : 9 Oct 2017


Publication Name : Sustainability impact assessments of different urban short food supply chains: Examples from London, UK
Publication URL : https://pureportal.coventry.ac.uk/en/publications/sustainability-impact-assessments-of-different-urban-short-food-s
CU Author : Ulrich Schmutz
Date : 11 Nov 2017


Publication Name : The Brookside Farm Wetland Ecosystem Treatment (WET) System: A Low-Energy Methodology for Sewage Purification, Biomass Production (Yield), Flood Resilience and Biodiversity Enhancement
Publication URL : https://pureportal.coventry.ac.uk/en/publications/the-brookside-farm-wetland-ecosystem-treatment-wet-system-a-low

link https://pureportal.coventry.ac.uk/en/persons/michelle-scott
None
link https://pureportal.coventry.ac.uk/en/persons/steve-scott
None
Publication Name : It Was This Wing Wasn’t It? Identifying the Importance of Verbal Communication in Aviation Maintenance
Publication URL : https://pureportal.coventry.ac.uk/en/publications/it-was-this-wing-wasnt-it-identifying-the-importance-of-verbal-co
CU Author : Steve Scott
Date : 19 Jan 2023


Publication Name : Identifying the Important Contributory Factors From Maintenance Error Decision Aid (MEDA) Data
Publication URL : https://pureportal.coventry.ac.uk/en/publications/identifying-the-important-contributory-factors-from-maintenance-e
CU Author : Steve Scott
Date : 5 Jul 2022


Publication Name : Perceptions of Just Culture Between Pilots and Managers: Evaluation of Airlines in the EU, Middle East, and Asia/Pacific Regions
Publication URL : https://pureportal.coventry.ac.uk/en/publications/perceptions-of-just-culture-between-pilots-and-manager

TimeoutException: Message: timeout: Timed out receiving message from renderer: 298.009
  (Session info: headless chrome=113.0.5672.126)
Stacktrace:
0   chromedriver                        0x0000000102a2b8ac chromedriver + 4257964
1   chromedriver                        0x0000000102a23f40 chromedriver + 4226880
2   chromedriver                        0x00000001026609d4 chromedriver + 281044
3   chromedriver                        0x000000010264a84c chromedriver + 190540
4   chromedriver                        0x000000010264a574 chromedriver + 189812
5   chromedriver                        0x0000000102649198 chromedriver + 184728
6   chromedriver                        0x0000000102649620 chromedriver + 185888
7   chromedriver                        0x000000010265722c chromedriver + 242220
8   chromedriver                        0x000000010266ab8c chromedriver + 322444
9   chromedriver                        0x0000000102649b20 chromedriver + 187168
10  chromedriver                        

In [62]:
import pandas as pd

In [107]:
links = pd.read_csv('Authors_URL.txt')

In [108]:
links = links.values.tolist()

In [102]:
# links = [links[0]]

In [109]:
len(links)

300

In [110]:
def initCrawlerScraper(seed):
    # Initialize driver for Chrome
    webOpt = webdriver.ChromeOptions()
    webOpt.add_experimental_option('excludeSwitches', ['enable-logging'])
    webOpt.add_argument('--ignore-certificate-errors')
    webOpt.add_argument('--incognito')
    webOpt.add_argument('--headless')
    
    driver = webdriver.Chrome(ChromeDriverManager().install(), options=webOpt)
    driver.get(seed)  # Start with the original link
    
    pub_data = []
    print("Crawler has found ", len(links), " pureportal profiles")
#     write_authors(Links, 'Authors_URL.txt')
    
    
    print("Scraping publication data for ", len(links), " pureportal profiles...")
    count = 0
    for link in links:
        # Visit each link to get data
        time.sleep(1)
        result = driver.get(link[0])
        driver.get(link[0])
        try:
            if driver.find_elements(By.CSS_SELECTOR,".portal_link.btn-primary.btn-large"):
                element = driver.find_elements(By.CSS_SELECTOR,".portal_link.btn-primary.btn-large")
                for a in element:
                    if "research output".lower() in a.text.lower():
                        driver.execute_script("arguments[0].click();", a)
                        driver.get(driver.current_url)
                        # Get name of Author
                        name = driver.find_element(By.CSS_SELECTOR,"div[class='header person-details']>h1")
                        r = requests.get(driver.current_url)
                        # Parse all the data via BeautifulSoup
                        soup = BeautifulSoup(r.content, 'lxml')

                        # Extracting publication name, publication url, date and CU Authors
                        table = soup.find('ul', attrs={'class': 'list-results'})
                        if table != None:
                            for row in table.findAll('div', attrs={'class': 'result-container'}):
                                data = {}
                                data['name'] = row.h3.a.text
                                data['pub_url'] = row.h3.a['href']
                                date = row.find("span", class_="date")

                                rowitem = row.find_all(['div'])
                                span = row.find_all(['span'])
                                data['cu_author'] = name.text
                                data['date'] = date.text
                                print("Publication Name :", row.h3.a.text)
                                print("Publication URL :", row.h3.a['href'])
                                print("CU Author :", name.text)
                                print("Date :", date.text)
                                print("\n")
                                pub_data.append(data)
            else:
                # Get name of Author
                name = driver.find_element(By.CSS_SELECTOR,"div[class='header person-details']>h1")
                r = requests.get(link)
                # Parse all the data via BeautifulSoup
                soup = BeautifulSoup(r.content, 'lxml')
                # Extracting publication name, publication url, date and CU Authors
                table = soup.find('div', attrs={'class': 'relation-list relation-list-publications'})
                if table != None:
                    for row in table.findAll('div', attrs={'class': 'result-container'}):
                        data = {}
                        data["name"] = row.h3.a.text
                        data['pub_url'] = row.h3.a['href']
                        date = row.find("span", class_="date")
                        rowitem = row.find_all(['div'])
                        span = row.find_all(['span'])
                        data['cu_author'] = name.text
                        data['date'] = date.text
                        print("Publication Name :", row.h3.a.text)
                        print("Publication URL :", row.h3.a['href'])
                        print("CU Author :", name.text)
                        print("Date :", date.text)
                        print("\n")
                        pub_data.append(data)
        except Exception:
            continue

    print("Crawler has scrapped data for ", len(pub_data), " pureportal publications")
    driver.quit()
    # Writing all the scraped results in a file with JSON format
    with open('scraper_results.json', 'w') as f:
        ujson.dump(pub_data, f)

In [ ]:
initCrawlerScraper('https://pureportal.coventry.ac.uk/en/organisations/coventry-university/persons/')

/var/folders/3y/yxfc9cms7ss262pddd2ymh_40000gp/T/ipykernel_1602/1229254135.py:9: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(ChromeDriverManager().install(), options=webOpt)


Crawler has found  300  pureportal profiles
Scraping publication data for  300  pureportal profiles...
Publication Name : Is Maritime Security Gender-blind?
Publication URL : https://pureportal.coventry.ac.uk/en/publications/is-maritime-security-gender-blind
CU Author : Ioannis Chapsos
Date : Jan 2023


Publication Name : Protective Security at Sea: A Counter Terrorism Framework  for Cruise and Passenger Ships
Publication URL : https://pureportal.coventry.ac.uk/en/publications/protective-security-at-sea-a-counter-terrorism-framework-for-crui
CU Author : Ioannis Chapsos
Date : 3 Jan 2023


Publication Name : Ships Without Crews: IMO and UK responses to cybersecurity, technology, law and regulation of Maritime Autonomous Surface Ships (MASS)
Publication URL : https://pureportal.coventry.ac.uk/en/publications/ships-without-crews-imo-and-uk-responses-to-cybersecurity-technol
CU Author : Ioannis Chapsos
Date : 24 May 2023


Publication Name : Robot Boats: Use of Autonomous ‘Ships’ in Law En

CU Author : Sue Charlesworth
Date : 12 Apr 2018


Publication Name : The necessity for urban wastewater collection, treatment, and disposal
Publication URL : https://pureportal.coventry.ac.uk/en/publications/the-necessity-for-urban-wastewater-collection-treatment-and-dispo
CU Author : Sue Charlesworth
Date : 16 Oct 2018


Publication Name : UK and EU water policy as an instrument of urban pollution
Publication URL : https://pureportal.coventry.ac.uk/en/publications/uk-and-eu-water-policy-as-an-instrument-of-urban-pollution
CU Author : Sue Charlesworth
Date : 16 Oct 2018


Publication Name : Urban aquatic pollution in Brazil
Publication URL : https://pureportal.coventry.ac.uk/en/publications/urban-aquatic-pollution-in-brazil
CU Author : Sue Charlesworth
Date : 16 Oct 2018


Publication Name : Urban pollution: Science and management
Publication URL : https://pureportal.coventry.ac.uk/en/publications/urban-pollution-science-and-management
CU Author : Sue Charlesworth
Date : 16 Oct 2018




Publication Name : A Comparative Study of Chinese Test-takers’ Writing Performance in Integrated and Discrete Tasks: Scores and Recurrent Word Combinations in PTE Academic
Publication URL : https://pureportal.coventry.ac.uk/en/publications/a-comparative-study-of-chinese-test-takers-writing-performance-in
CU Author : Yu-Hua Chen
Date : 25 May 2022


Publication Name : Developing a Multimodal Corpus of L2 Academic English from an English Medium Instruction University in China
Publication URL : https://pureportal.coventry.ac.uk/en/publications/developing-a-multimodal-corpus-of-l2-academic-english-from-an-eng
CU Author : Yu-Hua Chen
Date : 2 Sept 2022


Publication Name : Dancing K-Pop with Chinese and “English in Class Please”: Policy Negotiations as Relational-Languaging Episodes
Publication URL : https://pureportal.coventry.ac.uk/en/publications/dancing-k-pop-with-chinese-and-english-in-class-please-policy-neg
CU Author : Yu-Hua Chen
Date : Aug 2021


Publication Name : The EMI campus a

Publication Name : 台湾嘉义县龙山小学防灾教育实施成效评估工程研究
Publication URL : https://pureportal.coventry.ac.uk/en/publications/%E5%8F%B0%E6%B9%BE%E5%98%89%E4%B9%89%E5%8E%BF%E9%BE%99%E5%B1%B1%E5%B0%8F%E5%AD%A6%E9%98%B2%E7%81%BE%E6%95%99%E8%82%B2%E5%AE%9E%E6%96%BD%E6%88%90%E6%95%88%E8%AF%84%E4%BC%B0%E5%B7%A5%E7%A8%8B%E7%A0%94%E7%A9%B6
CU Author : Yung-Fang Chen
Date : 2012


Publication Name : Business continuity planning
Publication URL : https://pureportal.coventry.ac.uk/en/publications/business-continuity-planning
CU Author : Yung-Fang Chen
Date : 2011


Publication Name : Fundraising cycle
Publication URL : https://pureportal.coventry.ac.uk/en/publications/fundraising-cycle
CU Author : Yung-Fang Chen
Date : 2011


Publication Name : Kobe earthquake
Publication URL : https://pureportal.coventry.ac.uk/en/publications/kobe-earthquake-2
CU Author : Yung-Fang Chen
Date : 2011


Publication Name : Optimal human resource allocation model:  A case study of Taiwan fire service
Publication URL : https://purep

...

Publication Name : STAT5 signaling in kisspeptin cells regulates the timing of puberty
Publication URL : https://pureportal.coventry.ac.uk/en/publications/stat5-signaling-in-kisspeptin-cells-regulates-the-timing-of-puber
CU Author : Isadora Clivatti Furigo
Date : 15 Jun 2017


Publication Name : Brain STAT5 signaling and behavioral control
Publication URL : https://pureportal.coventry.ac.uk/en/publications/brain-stat5-signaling-and-behavioral-control
CU Author : Isadora Clivatti Furigo
Date : 15 Dec 2016


Publication Name : Cdc2-like kinase 2 in the hypothalamus is necessary to maintain energy homeostasis
Publication URL : https://pureportal.coventry.ac.uk/en/publications/cdc2-like-kinase-2-in-the-hypothalamus-is-necessary-to-maintain-e
CU Author : Isadora Clivatti Furigo
Date : 13 Oct 2016


Publication Name : Changes in Leptin Signaling by SOCS3 Modulate Fasting-Induced Hyperphagia and Weight Regain in Mice
Publication URL : https://pureportal.coventry.ac.uk/en/publications/changes-

Publication Name : The ‘Gift Exchange’: a metaphor for understanding the relationship between educator commitment and student effort on placement
Publication URL : https://pureportal.coventry.ac.uk/en/publications/the-gift-exchange-a-metaphor-for-understanding-the-relationship-b-2
CU Author : Deanne Clouder
Date : 2014


Publication Name : Collaborative health and social care, and the role of interprofessional education
Publication URL : https://pureportal.coventry.ac.uk/en/publications/collaborative-health-and-social-care-and-the-role-of-interprofess-2
CU Author : Deanne Clouder
Date : Mar 2013


Publication Name : Enhancing Guidance for Disabled People Wanting to Become Health and Social Care Professionals Report
Publication URL : https://pureportal.coventry.ac.uk/en/publications/enhancing-guidance-for-disabled-people-wanting-to-become-health-a-3
CU Author : Deanne Clouder
Date : 13 Dec 2013


Publication Name : Introduction
Publication URL : https://pureportal.coventry.ac.uk/en/publ

CU Author : Jane Coad
Date : 2016


Publication Name : An exploration of the data collection methods utilised with children, teenagers and young people (CTYPs)
Publication URL : https://pureportal.coventry.ac.uk/en/publications/an-exploration-of-the-data-collection-methods-utilised-with-child-2
CU Author : Jane Coad
Date : 1 Mar 2015


Publication Name : Be my guest! Challenges and practical solutions of undertaking interviews with children in the home setting
Publication URL : https://pureportal.coventry.ac.uk/en/publications/be-my-guest-challenges-and-practical-solutions-of-undertaking-int-2
CU Author : Jane Coad
Date : 1 Dec 2015


Publication Name : Blended foods for tube-fed children – a safe and realistic option? Blended foods for tube-fed children – a safe and realistic option? 
Publication URL : https://pureportal.coventry.ac.uk/en/publications/blended-foods-for-tube-fed-children-a-safe-and-realistic-option-b
CU Author : Jane Coad
Date : 2015


Publication Name : Exploring the 

Publication Name : Effect of frequency and power on the piezocatalytic and sonochemical degradation of dyes in water
Publication URL : https://pureportal.coventry.ac.uk/en/publications/effect-of-frequency-and-power-on-the-piezocatalytic-and-sonochemi
CU Author : Andrew Cobley
Date : 15 May 2023


Publication Name : Selective soldering nozzles: insights into wear mechanisms and future developments
Publication URL : https://pureportal.coventry.ac.uk/en/publications/selective-soldering-nozzles-insights-into-wear-mechanisms-and-fut
CU Author : Andrew Cobley
Date : 24 Jan 2023


Publication Name : Using fish scales as a new biosorbent for adsorption of nickel and copper ions from wastewater and investigating the effects of electric and magnetic fields on the adsorption process
Publication URL : https://pureportal.coventry.ac.uk/en/publications/using-fish-scales-as-a-new-biosorbent-for-adsorption-of-nickel-an
CU Author : Andrew Cobley
Date : Mar 2023


Publication Name : Selective Electroles

CU Author : Andrew Cobley
Date : 24 Feb 2016


Publication Name : Bismuth-based composite coating for overlay applications in plain bearings
Publication URL : https://pureportal.coventry.ac.uk/en/publications/bismuth-based-composite-coating-for-overlay-applications-in-plain-2
CU Author : Andrew Cobley
Date : 20 Jul 2016


Publication Name : The Effect of Mixing and Degassing Conditions on the Properties of Epoxy/Anhydride Resin System
Publication URL : https://pureportal.coventry.ac.uk/en/publications/the-effect-of-mixing-and-degassing-conditions-on-the-properties-o
CU Author : Andrew Cobley
Date : 20 Jun 2016


Publication Name : Ultrasound assisted electrodeposition of Zn and Zn-TiO2 coatings
Publication URL : https://pureportal.coventry.ac.uk/en/publications/ultrasound-assisted-electrodeposition-of-zn-and-zn-tio2-coatings-2
CU Author : Andrew Cobley
Date : 20 Apr 2016


Publication Name : A plain bearing with improved interlayer
Publication URL : https://pureportal.coventry.ac.uk/en

In [ ]:
import schedule
import time

schedule.every().monday.at("12:00").do(
    lambda: initCrawlerScraper("https://pureportal.coventry.ac.uk/en/organisations/coventry-university/persons/")
)


while True:
    schedule.run_pending()
    time.sleep(1)